In [1]:
import pandas as pd
import param as pm
import panel as pn
import hvplot.pandas
import holoviews as hv
import numpy as np

pn.extension()

In [6]:
class Fundraising(pm.Parameterized):
    total_raised = pm.Number(1e6, bounds=(1e5, 1e7), precedence=-1)
    hatch_tribute = pm.Number(0.05, bounds=(0,1), precedence=-1)
    hatch_price = pm.Number(1, bounds=(0.5,2), precedence=-1)
    initial_price = pm.Number(2, bounds=(1,4))
    expected_growth = pm.Number(200, bounds=(1,300))
    reserve_ratio = pm.Number(0.1, bounds=(0,1))
    entry_tribute = pm.Number(0.0, bounds=(0,0.5), precedence=-1)
    exit_tribute = pm.Number(0.0, bounds=(0,0.5), precedence=-1)
    token_supply = pm.Number(0)
    reserve_balance = pm.Number(0)
    
    def xrate(self):
        return 1 / self.hatch_price
    
    def growth(self):
        return self.expected_growth
    
    def pctOffered(self):
        return 1
    
    def pctBeneficiary(self):
        return self.hatch_tribute
    
    def sSupply(self):
        return self.total_raised * self.xrate()
    
    def sBalance(self):
        return self.total_raised * (1 - self.hatch_tribute)
    
    def sPrice(self):
        return self.initial_price
    
    def sMarketCap(self):
        return self.sSupply() * self.sPrice()
    
    def eMarketCap(self):
        return self.sMarketCap() * self.growth()
    
    def ePrice(self):
        return self.sPrice() * np.sqrt(self.growth())
    
    def ppSupply(self):
#         ppSupply = (ePrice / (eMarketCap ** (1 - reserveRatio) * (sPrice ** reserveRatio))) ** (1 / (reserveRatio - 1))
        return (self.ePrice() / (self.eMarketCap()**(self.reserve_ratio - 1) * (self.sPrice() ** self.reserve_ratio))) ** (1 / (self.reserve_ratio - 1))
                                                   
    def vSupply(self):
        return self.ppSupply() - self.sSupply()
    
    def ppBalance(self):
        return self.sPrice() * self.ppSupply() * self.reserve_ratio
    
    def vBalance(self):
        return self.ppBalance() - self.sBalance()
    
    def get_outputs(self):
        outputs = pd.DataFrame({
            "sSupply": f.sSupply(),
            "sBalance": f.sBalance(),
            "sPrice": f.sPrice(),
            "sMarketcap": f.sMarketCap(),
            "ePrice": f.ePrice(),
            "eMarketCap": f.eMarketCap(),
            "ppSupply": f.ppSupply(),
            "vSupply": f.vSupply(),
            "ppBalance": f.ppBalance(),
            "vBalance": f.vBalance(),
        }, index=['Value'])
        return outputs
    
    def view_outputs(self):
        outputs = self.get_outputs()
        return outputs.apply(lambda x: round(x, 2)).T

    def buy_amount(self, supply, collateral, pay_amount, reserve_ratio):
        # buyAmt = tokenSupply * ((1 + amtPaid / collateral)^CW — 1)
        return supply * ((1 + pay_amount / collateral)**reserve_ratio - 1)
    
    def sell_amount(self, supply, collateral, sell_amount, reserve_ratio):
        # sellAmt = collateral * ((1 + tokensSold / totalSupply)^(1/CW) — 1)
        return collateral * ((1 + sell_amount / supply)**(1/reserve_ratio) - 1)
    
    def make_buy_order(self, buy_amount):
        fee = buy_amount * self.entry_tribute
        buy_amount = buy_amount - fee
        self.reserve_balance += buy_amount
        collateral_supply = self.token_supply + self.vSupply()
        collateral_balance = self.reserve_balance + self.vBalance()
        return_amount = self.buy_amount(collateral_supply, collateral_balance, buy_amount, self.reserve_ratio)
        self.token_supply += return_amount
        return return_amount
        
    def make_sell_order(self, sell_amount):
        collateral_supply = self.token_supply + self.vSupply()
        collateral_balance = self.reserve_balance + self.vBalance()
        return_amount = self.sell_amount(collateral_supply, collateral_balance, sell_amount, self.reserve_ratio)
        fee = return_amount * self.exit_tribute 
        self.token_supply -= sell_amount
        self.reserve_balance -= return_amount - fee
        return return_amount - fee    
    
    def get_buy_price(self, token_supply=None, reserve_balance=None, amount_wxdai=1e-6):
        if token_supply is None:
            token_supply = self.token_supply
        if reserve_balance is None:
            reserve_balance = self.reserve_balance
        return amount_wxdai / self.buy_amount(token_supply + self.vSupply(), reserve_balance + self.vBalance(), amount_wxdai, self.reserve_ratio)
    
    def get_sell_price(self, token_supply=None, reserve_balance=None, amount_tec=1e-6):
        if token_supply is None:
            token_supply = self.token_supply
        if reserve_balance is None:
            reserve_balance = self.reserve_balance
        return self.sell_amount(token_supply + self.vSupply(), reserve_balance + self.vBalance(), amount_tec, self.reserve_ratio) / amount_tec
    
    def view_price_supply_chart(self):
        x = np.linspace(0,1e6,1000)
        y = self.get_buy_price(token_supply=x)
        df = pd.DataFrame(zip(x,y),columns=['supply','price'])
        return df.hvplot.area(x='supply',y='price')

In [7]:
f = Fundraising()

pn.Row(f, pn.Column(f.view_price_supply_chart, f.view_outputs))

Row
    [0] Column(margin=5, name='Fundraising', width=300)
        [0] StaticText(value='<b>Fundraising</b>')
        [1] FloatSlider(end=4, name='Initial price', start=1, value=2)
        [2] FloatSlider(end=300, name='Expected growth', start=1, value=200)
        [3] FloatSlider(name='Reserve ratio', value=0.1)
        [4] FloatInput(name='Token supply')
        [5] FloatInput(name='Reserve balance')
    [1] Column
        [0] ParamMethod(method)
        [1] ParamMethod(method)

In [119]:
class Fundraising(pm.Parameterized):
    total_raised = pm.Number(1e6, bounds=(1e5, 1e7), precedence=-1)
    hatch_tribute = pm.Number(0.05, bounds=(0,1), precedence=-1)
    hatch_price = pm.Number(1, bounds=(0.5,2), precedence=-1)
    initial_price = pm.Number(2, bounds=(1,4))
    expected_growth = pm.Number(200, bounds=(1,300))
    reserve_ratio = pm.Number(0.1, bounds=(0,1))
    entry_tribute = pm.Number(0.0, bounds=(0,0.5), precedence=-1)
    exit_tribute = pm.Number(0.0, bounds=(0,0.5), precedence=-1)
    token_supply = pm.Number(0)
    reserve_balance = pm.Number(0)
    
    def __init__(self, **params):
        super(Fundraising, self).__init__(**params)
        
    def sSupply(self):
        xrate = 1 / self.hatch_price
        return self.total_raised * xrate
    
    def sBalance(self):
        return self.total_raised * (1 - self.hatch_tribute)
    
    def sMarketCap(self):
        return self.sSupply() * self.initial_price
    
    def eMarketCap(self):
        return self.sMarketCap() * self.expected_growth
    
    def ePrice(self):
        return self.initial_price * np.sqrt(self.expected_growth)
    
    def ppSupply(self):
#         ppSupply = (ePrice / (eMarketCap ** (1 - reserveRatio) * (sPrice ** reserveRatio))) ** (1 / (reserveRatio - 1))
        return (self.ePrice() / (self.eMarketCap()**(1 - self.reserve_ratio) * (self.initial_price ** self.reserve_ratio))) ** (1 / (self.reserve_ratio - 1))
                                                
    def ppBalance(self):
        return self.initial_price * self.ppSupply() * self.reserve_ratio
    
    def vSupply(self):
        return self.ppSupply() - self.sSupply()
    
    def vBalance(self):
        return self.ppBalance() - self.sBalance()
    
    def get_outputs(self):
        outputs = pd.DataFrame({
            "Starting": [f.initial_price, f.sSupply(), f.sMarketCap(), f.sBalance()],
            "Expected": [f.ePrice(), 0, f.eMarketCap(), 0],
            'PP': [0, f.ppSupply(), 0, f.ppBalance()],
            'Virtual': [0, f.vSupply(), 0, f.vBalance()],
        }, index=['Price','Supply','MarketCap','Balance'])
        return outputs
    
    def view_outputs(self):
        outputs = self.get_outputs()
        outputs = outputs.T
        for c in outputs.columns:
            outputs[c] = outputs[c].apply(lambda x: "{:,.2f}".format(x))
        return outputs.reset_index().hvplot.table()

    def buy_amount(self, supply, collateral, pay_amount, reserve_ratio):
        # buyAmt = tokenSupply * ((1 + amtPaid / collateral)^CW — 1)
        return supply * ((1 + pay_amount / collateral)**reserve_ratio - 1)
    
    def sell_amount(self, supply, collateral, sell_amount, reserve_ratio):
        # sellAmt = collateral * ((1 + tokensSold / totalSupply)^(1/CW) — 1)
        return collateral * ((1 + sell_amount / supply)**(1/reserve_ratio) - 1)
    
    def make_buy_order(self, buy_amount):
        fee = buy_amount * self.entry_tribute
        buy_amount = buy_amount - fee
        self.reserve_balance += buy_amount
        collateral_supply = self.token_supply + self.vSupply()
        collateral_balance = self.reserve_balance + self.vBalance()
        return_amount = self.buy_amount(collateral_supply, collateral_balance, buy_amount, self.reserve_ratio)
        self.token_supply += return_amount
        return return_amount
        
    def make_sell_order(self, sell_amount):
        collateral_supply = self.token_supply + self.vSupply()
        collateral_balance = self.reserve_balance + self.vBalance()
        return_amount = self.sell_amount(collateral_supply, collateral_balance, sell_amount, self.reserve_ratio)
        fee = return_amount * self.exit_tribute 
        self.token_supply -= sell_amount
        self.reserve_balance -= return_amount - fee
        return return_amount - fee    
    
    def get_buy_price(self, token_supply=None, reserve_balance=None, amount_wxdai=1e-6):
        if token_supply is None:
            token_supply = self.token_supply
        if reserve_balance is None:
            reserve_balance = self.reserve_balance
        return amount_wxdai / self.buy_amount(token_supply + self.vSupply(), reserve_balance + self.vBalance(), amount_wxdai, self.reserve_ratio)
    
    def get_sell_price(self, token_supply=None, reserve_balance=None, amount_tec=1e-6):
        if token_supply is None:
            token_supply = self.token_supply
        if reserve_balance is None:
            reserve_balance = self.reserve_balance
        return self.sell_amount(token_supply + self.vSupply(), reserve_balance + self.vBalance(), amount_tec, self.reserve_ratio) / amount_tec
    
    def view_price_supply_chart(self):
        x = np.linspace(0,1e6,1000)
        y = self.get_buy_price(token_supply=x)
        df = pd.DataFrame(zip(x,y),columns=['supply','price'])
        return df.hvplot.area(x='supply',y='price')

In [120]:
f = Fundraising()

pn.Row(f, pn.Column(f.view_price_supply_chart, f.view_outputs))

Row
    [0] Column(margin=5, name='Fundraising', width=300)
        [0] StaticText(value='<b>Fundraising</b>')
        [1] FloatSlider(end=4, name='Initial price', start=1, value=2)
        [2] FloatSlider(end=300, name='Expected growth', start=1, value=200)
        [3] FloatSlider(name='Reserve ratio', value=0.1)
        [4] FloatInput(name='Token supply')
        [5] FloatInput(name='Reserve balance')
    [1] Column
        [0] ParamMethod(method)
        [1] ParamMethod(method)

In [96]:
expected_growth = np.linspace(f.param['expected_growth'].bounds,100)
reserve_ratio = np.linspace(f.param['expected_growth'].bounds,100)

In [16]:
collateral = []
supply = []

for i in range(int(1e5)):
    f.make_buy_order(1)
    collateral.append(f.reserve_balance)
    supply.append(f.token_supply)

In [17]:
df = pd.DataFrame(zip(collateral,supply),columns=['collateral','supply'])

In [18]:
df.hvplot.line(x='collateral',y='supply')

:Curve   [collateral]   (supply)

In [19]:
df['price'] = df.apply(lambda x: f.get_buy_price(token_supply=x['supply'], reserve_balance=x['collateral']), axis=1)

In [20]:
df.hvplot.line(x='supply',y='price')

:Curve   [supply]   (price)

ZeroDivisionError: division by zero

In [22]:
f.get_buy_price()

1.308296847021554

In [23]:
f.get_sell_price()

1.3064643126662632

In [12]:
f.make_buy_order(100)

76.47313509812193

In [13]:

collateral_supply = 
collateral_balance = 
return_amount = self.buy_amount(collateral_supply, collateral_balance, buy_amount, self.reserve_ratio)

SyntaxError: invalid syntax (<ipython-input-13-b082092d4907>, line 1)

In [ ]:
100 / 2.407756641001558